In [79]:
import os
import pickle
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import numpy as np
import pandas as pd
from konlpy.tag import Okt
import random
import re

In [2]:
df = pd.read_csv('./travel_spot.csv', index_col=0)
df = df.fillna('')

In [3]:
df2 = pd.read_csv('./travel_spot.csv', index_col=0)
df2 = df2.fillna('')

In [4]:
df2['city'] = '전체'

In [5]:
joined_df = pd.concat([df,df2], axis=0, ignore_index=True)

In [6]:
len(df),len(df2),len(joined_df)

(10517, 10517, 21034)

In [7]:
joined_df['vec'] = joined_df['catchtitle'].apply(lambda x: x[:100]) + joined_df['treatMenu'].apply(lambda x: x[:200]) + joined_df['tagName'].apply(lambda x: x[:200]) + joined_df['overView'].apply(lambda x: x[:200])

In [8]:
spot_df = joined_df[joined_df['contentType'] != 39]
food_df = joined_df[joined_df['contentType'] == 39]
spot_df.__len__(), food_df.__len__()

(9268, 11766)

In [119]:
len(spot_df), len(food_df)

(9268, 11766)

In [12]:
okt = Okt()

In [25]:
spot_df[spot_df['city'] != '전체']['vec'].tolist()[0]

'숲과 문화가 어우러지는 서울의 대표적인 녹색쉼터가족여행,걷기길,관광지,데이트코스,반려동물동반여행지,생태관광지,서울숲,수도권,수도권반려동물여행지,아이와함께,연인과함께,연중무휴,피크닉,한국관광100선,휴식공간,휴식여행,휴식하기,휴식하기좋은곳2005년 6월 18일 ‘서울숲’ 개원 이전까지는 임금의 사냥터였고 1908년 설치된 서울 최초의 상수원 수원지였으며, 이후 경마장, 골프장으로 활용되기도 했다. 현재 ‘서울숲’은 18만 평 규모의 4개 테마공원으로서 환경친화적인 대규모 휴식 공간으로 탈바꿈하였다. 영국의 하이드파크(Hyde Park), 뉴욕의 센트럴파크(Central Park)와 같이 서'

In [14]:
spot_df['city'].unique()

array(['서울', '인천', '대전', '대구', '광주', '부산', '울산', '세종시', '경기', '강원', '충북',
       '충남', '경북', '경남', '전북', '전남', '제주', '전체'], dtype=object)

In [78]:
test = ['설치', '기도', '활용', '여행지', '환경', '파크', '최초', '영국', '아이', '뉴욕', '연중', '대표', '여행', '공간', '문화', '사냥터', '데이트', '이전', '경마장', '생태관광', '관광지', '휴식', '수원지', '연인', '상수', '대규모', '이드', '임금', '골프장', '서울숲', '서울', '녹색', '가족', '센트럴', '수도권', '피크닉', '관광', '이후', '테마', '현재', '코스', '규모', '한국', '반려동물', '공원', '개원', '탈바꿈']
len(test)

47

In [62]:

test.append(['a','b'])
test

['a', 'a', 'a', 'a', 'b', ['a', 'b'], ['a', 'b'], ['a', 'b']]

In [100]:
len(tag_list_all)

4634

In [99]:
# spot 학습

vectorizer_spot = TfidfVectorizer(sublinear_tf = True,max_features = 60)
vectorizer_food = TfidfVectorizer(sublinear_tf = True,max_features = 60)



# 전체 도시에 대한 TF-IDF 행렬 계산
tag_list_all = []
for i in spot_df[spot_df['city'] != '전체']['vec'].tolist():
    tag_list_all.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(len(tag_list_all))

matrix_spot = vectorizer_spot.fit_transform(tag_list_all)

# 각 도시에 대한 TF-IDF 행렬 계산
city_matrices_spot = {}
for city in spot_df['city'].unique():
    tag_list_city = []
    city_df = spot_df[spot_df['city'] == city]
    
    for i in city_df['vec'].tolist():
        tag_list_city.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        len(tag_list_city)

    city_matrices_spot[city] = vectorizer_spot.transform(tag_list_city)


설치 기도 활용 여행지 환경 파크 최초 영국 아이 뉴욕 연중 대표 여행 공간 문화 사냥터 데이트 이전 경마장 생태관광 관광지 휴식 수원지 연인 상수 대규모 이드 임금 골프장 서울숲 서울 녹색 가족 센트럴 수도권 피크닉 관광 이후 테마 현재 코스 규모 한국 반려동물 공원 개원 탈바꿈
1
길상사 중턱 종교 역사 산사 시주 원각 당시 자연환경 사찰 상화 김영한 성북동 체험 위치 연중 불도 여행 공간 문화 불교 예전 주인 관광지 휴식 비롯 연속 관광객 시가 외국인 도심 서울 프로그램 자연 수도권 건물 마련 자리 한국 대지 개원 수련 전통
2
상설 장악 체결 침략 돌파구 기도 투어 중국 을사조약 나들이 맛집 최초 시장 야간 남대문시장 친구 아이 우리 우리나라 먹거리 각축 정세 따라서 실질 정책 여행 쇼핑 경제 데이트 일본 경영 종로 홀로 혼미 주권 로서 국내 연인 강세 나라 도심 가족 수도권 풍전등화 관광 거듭 행사 코스 광장시장 구한말 국운 고종 전통
3
드라이브 사업 시민 역사 체험학습 나들이 사산 목장 야경 야간 보급 친구 우유 아이 지형 모습 진행 성곽 수립 여행 복원 문화 중심 데이트 낙타산 본래 관광지 계획 산이 연인 하나로 청룡 일대 낙타 아파트 해당 밀집 일환 왕실 걷기 서울 가족 낙산 수도권 이후 관광 서울시 코스 타락 공원 주택 힐링
4
북쪽 사랑 기도 자랑 궁궐 투어 당일치기 역사 동궐 교과서 근교 태조 정종 친구 북궐 체험 아이 이성계 창덕궁 위치 여행 인생 문화 법궁 다섯 시절 경희궁 세조 성종 세종 즉위 종로 유적지 관광지 으뜸 근정전 연인 건축 통역사 조선왕조 가운데 서울 가족 수도권 불리 관광 단종 규모 코스 고궁 이나 한국 경복궁 우리
5
전쟁 재래시장 투어 부근 체험학습 오감 모두 공지 생활 나들이 맛집 시장 한약재 친구 아이 먹거리 이름 농산물 여행 쇼핑 북부 사람 상품 통해 청량리역 등지 알리 데이트 시작 각종 레이스 홀로 연인 장사 강원도 개설 대규모 판매 반입 회복 위해 노소 서울 남녀 가족 동시 수도권 이후 자연 열차 코스 경기

In [102]:
# food 학습

# 전체 도시에 대한 TF-IDF 행렬 계산
tag_list_all_food = []
for i in food_df[food_df['city'] != '전체']['vec'].tolist():
    tag_list_all_food.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(len(tag_list_all_food))


matrix_food = vectorizer_food.fit_transform(tag_list_all_food)

# 각 도시에 대한 TF-IDF 행렬 계산
city_matrices_food = {}
for city in food_df['city'].unique():
    tag_list_city_food = []
    city_df = food_df[food_df['city'] == city]
    
    for i in city_df['vec'].tolist():
        tag_list_city_food.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        len(tag_list_city_food)
        
    city_matrices_food[city] = vectorizer_food.transform(tag_list_city_food)


백련산 인근 꼬리 선택 설렁탕 맛집 고기 가로수길 도가니 수육 은평구 구이 사용 새절역 돌판 대표 소면 대추 이상 운영 메뉴인 출구 희모 육수 시간 꼬리곰탕 우려 깃밥 곰탕 황태 신사동 밑반찬 음식 불광천 서울 중이 주문 양지 호선 전통
1
방문 메뉴 숙성 그린 소갈비 초등학교 점심 제생 부근 전통 가능 맛집 응암동 매우 포크 은평구 이용 물냉면 대표 매장 비빔냉면 출구 쌈밥 협소하 특선 주차장 뒤편 응암역 수제 전문점 응암 대중교통 음식 갈비 건물 호선 지하철
2
집의 메뉴 잠원동 허름 가지 식당 간장게장 설렁탕 고수 서초영 수육 자랑거리 골목 운영 깍두기 영동 겉절이 외관 신사동 건너편 서초 음식 김치 한자리 역시 신사역 국밥 호선
3
브랜드 메뉴 복림 한식 서울특별시 서울 음식 중구 전통 대표 튀김 전문점 신당동 떡볶이 추천 맛집
4
추억 메뉴 역사 민족 야채 빵집 체인점 이름 베이커리 사라다 대표 자태 먼저 이상 케익 데이트 활동 협회 발전 태극 분위기 고풍 학교 가장 대한민국 모나카 설립 버터 창업 동참 제과제빵 카스테라 위해 서울 음식 또한 이란 광복 제과 옛날 우리
5
검정 마늘 재료 삼계탕 대통령 생강 경복궁역 맛집 인삼 해물파전 신토 들깨 시내 사용 위치 호박 노무현 대표 대추 사람 호두 더욱 산배 오골계 종로 계승 토종닭 발전 소문 율무 유명 해바라기씨 양근 음식 서울 정도 토속 전통
6
메뉴 가이드 맛집 미쉐린 지로 다른 위치 냉면 평양 대표 달리 시작 어르신 약간 전문점 선정 불고기 부담 음식 가족 도전 을지로 초심자
7
수제비 볶음 쭈꾸미 공관 심심찮 벽돌 일본인 경복궁역 맛집 새알 한아름 파전 소개 삼청동 찹쌀 더위 연중 잡지 호박 가로수 먼저 계절 감자전 일본 종로 하차 국무총리 길이 색깔 가장 때로는 제비집 옹심이 음식점 음식 서울 수도권 지나 낙엽 건물 삼청터널 호선 경복궁 지하철
8
레저 와이키키 세트 크보 낭만 예약 한우 야외 캠핑 야경 친구 모터보트 선상 파라솔 숯불 위치 소고기 여행 데이트 수상 시간 마켓 상암동 이색 테이

In [123]:
len(tag_list_city_food), len(tag_list_city)

(5883, 4634)

In [117]:
len(np.argsort(cos_similarities_f[0])[::-1]), len(df_f)

(156, 196)

In [118]:
len(np.argsort(cos_similarities_s[0])), len(df_s)

(156, 156)

In [110]:
#test 부분
# vectorizer_spot.fit(tag_list_all)

area = '인천'
question = '친구 연인 맛집 치킨, 데이트 야경'

df_s = spot_df[spot_df['city']== f'{area}']
df_f = food_df[food_df['city'] == f'{area}']

question_tfidf_s = vectorizer_spot.transform(okt.nouns(f'{question}'))
question_tfidf_f = vectorizer_food.transform(okt.nouns(f'{question}'))

cos_similarities_s = linear_kernel(question_tfidf_s, city_matrices_spot[f'{area}'])
cos_similarities_f = linear_kernel(question_tfidf_f, city_matrices_spot[f'{area}'])

sorted_indices_s = np.argsort(cos_similarities_s[0])[::-1][:5]
sorted_indices_f = np.argsort(cos_similarities_f[0])[::-1][:5]


# 식당인 것, 아닌 

index_s = sorted_indices_s[0]
index_f = sorted_indices_f[0]

# for s in sorted_indices_s:
#     print('spot result')
#     print(str(df.iloc[s]['city']))
#     print(str(df.iloc[s]['title']))
#     print(float(cos_similarities_s[0][s]))
#     print(str(df.iloc[s]['catchtitle']))

for f in sorted_indices_f:
    print('spot result')
    print(str(df.iloc[f]['city']))
    print(str(df.iloc[f]['title']))
    print(float(cos_similarities_s[0][f]))
    print(str(df.iloc[f]['catchtitle']))
    print("---------")

spot result
인천
부평역사박물관
0.0
부평의 역사와 문화를 지키고 알리는 곳
---------
spot result
인천
선재도(선재도 어촌체험마을)
0.0
열린 바닷길 위를 반려동물도 함께 걸을 수 있는 곳
---------
spot result
인천
외포리선착장
0.0
젓갈과 일몰로 유명한 강화도 선착장
---------
spot result
인천
인천 신기시장
0.0

---------
spot result
인천
구월농산물도매시장
0.0

---------


In [114]:
len(df_s)

156

In [112]:
len(cos_similarities_f[0])

156

In [66]:
vectorizer_spot.vocabulary_.items()

dict_items([('설치', 8468), ('기도', 2262), ('활용', 18101), ('여행지', 10708), ('환경', 18063), ('파크', 16517), ('최초', 15530), ('영국', 10911), ('아이', 9990), ('뉴욕', 3135), ('연중', 10831), ('대표', 3648), ('여행', 10701), ('공간', 1230), ('문화', 5544), ('사냥터', 7408), ('데이트', 3759), ('이전', 12622), ('경마장', 759), ('생태관광', 8097), ('관광지', 1395), ('휴식', 18328), ('수원지', 9104), ('연인', 10816), ('상수', 7927), ('대규모', 3442), ('이드', 12497), ('임금', 12910), ('골프장', 1163), ('서울숲', 8200), ('서울', 8197), ('녹색', 3025), ('가족', 149), ('센트럴', 8666), ('수도권', 8989), ('피크닉', 17029), ('관광', 1386), ('이후', 12678), ('테마', 16230), ('현재', 17688), ('코스', 15944), ('규모', 2013), ('한국', 17202), ('반려동물', 5963), ('공원', 1297), ('개원', 491), ('탈바꿈', 16095), ('길상사', 2382), ('중턱', 14486), ('종교', 14169), ('역사', 10719), ('산사', 7659), ('시주', 9529), ('원각', 11822), ('당시', 3387), ('자연환경', 13067), ('사찰', 7554), ('상화', 7999), ('김영한', 2448), ('성북동', 8534), ('체험', 15391), ('위치', 12035), ('불도', 7124), ('불교', 7110), ('예전', 11065), ('주인', 14318), ('비롯', 7242), ('

In [ ]:
# 저장
with open('travel_model_v2.pkl', 'wb') as file:
        pickle.dump({"spot":{
                "vectorizer": vectorizer_spot,
                "matrix": matrix_spot,
                "city_matrices": city_matrices_spot
        },"food":{
                "vectorizer": vectorizer_food,
                "matrix": matrix_food,
                "city_matrices": city_matrices_food
        }}, file)

In [ ]:
# 불러오기
with open('./travel_model_v2.pkl', 'rb') as file:
    loaded_data = pickle.load(file)
    
    vectorizer_spot = loaded_data["spot"]["vectorizer"]
    matrix_spot = loaded_data["spot"]["matrix"]
    city_matrices_spot = loaded_data["spot"]["city_matrices"]

    vectorizer_food = loaded_data["food"]["vectorizer"]
    matrix_food = loaded_data["food"]["matrix"]
    city_matrices_food = loaded_data["food"]["city_matrices"]

In [ ]:
area = '인천'
question = '캠핑'

df = spot_df[spot_df['city']== f'{area}']

question_tfidf = vectorizer_spot.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_spot[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1][:5]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]



print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



In [15]:
okt = Okt()
a = "샥스핀, 식사류해삼류,단품 요리 바닷가재 등  짬뽕 등  등"
b = "샥스핀, 해삼류, 바닷가재 등 단품 요리, 짜장면, 짬뽕 등 식사류 등"
A = [i for i in okt.morphs(a) if len(i) >1]
B = [i for i in okt.morphs(b) if len(i) >1]
vectorizer = TfidfVectorizer()
text = vectorizer_spot.transform(A)

cosine_similarities = cosine_similarity(text, matrix_spot)
cosine_similarities[0]

print(random.sample(A, len(A)))

['요리', '식사', '샥스핀', '짬뽕', '해삼류', '바닷가재']


In [38]:
len(spot_df), len(food_df), len(df3)

(9268, 11766, 21034)

In [82]:
tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in spot_df['tagName'].tolist()[:2]]
tag_list

['가족 여행 걷기길 관광지 데이트 코스 반려동물 여행지 생태관광 서울숲 수도권 수도권 반려동물 여행지 아이 함께 연인 함께 연중 피크닉 한국 관광 100 휴식 공간 휴식 여행 휴식 하기 휴식 하기 좋은',
 '관광지 길상사 서울 ), 불교 불교 문화 사찰 사찰 여행 산사 수도권 역사 연중 연속 으로 자연 좋은 자연환경 전통 사찰 종교 한국 불교 휴식 공간 휴식 여행 휴식 하기 휴식 하기 좋은']

In [39]:
vectorizer_spot = TfidfVectorizer()

tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in spot_df['tagName'].tolist()]
matrix_spot = vectorizer_spot.fit_transform(tag_list)

# 각 지역에 대한 TF-IDF 행렬 계산
city_matrices_spot = {}    
for city in spot_df['city'].unique():
    city_df = spot_df[spot_df['city'] == city]
    city_tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in city_df['tagName'].tolist()]
    city_matrices_spot[city] = vectorizer_spot.transform(city_tag_list)

In [5]:
vectorizer_food = TfidfVectorizer()

tag_list = [' '.join([j for j in okt.morphs(str(i)) if len(j) > 1]) for i in food_df['tf'].tolist()]
matrix_food = vectorizer_food.fit_transform(tag_list)

# 각 지역에 대한 TF-IDF 행렬 계산
city_matrices_food = {}    
for city in food_df['city'].unique():
    city_df = food_df[food_df['city'] == city]
    city_tag_list = [' '.join([j for j in okt.morphs(str(i)) if len(j) > 1]) for i in city_df['tf'].tolist()]
    city_matrices_food[city] = vectorizer_food.transform(city_tag_list)

In [6]:

# 저장
with open('travel_model_v2.pkl', 'wb') as file:
        pickle.dump({"spot":{
                "vectorizer": vectorizer_spot,
                "matrix": matrix_spot,
                "city_matrices": city_matrices_spot
        },"food":{
                "vectorizer": vectorizer_food,
                "matrix": matrix_food,
                "city_matrices": city_matrices_food
        }}, file)

In [4]:
with open('./travel_model_v2.pkl', 'rb') as file:
    loaded_data = pickle.load(file)
    
    vectorizer_spot = loaded_data["spot"]["vectorizer"]
    matrix_spot = loaded_data["spot"]["matrix"]
    city_matrices_spot = loaded_data["spot"]["city_matrices"]

    vectorizer_food = loaded_data["food"]["vectorizer"]
    matrix_food = loaded_data["food"]["matrix"]
    city_matrices_food = loaded_data["food"]["city_matrices"]

/home/doxg/.pyenv/versions/3.8.18/lib/python3.8/site-packages/sklearn/base.py:313: UserWarning: Trying to unpickle estimator TfidfTransformer from version 1.3.2 when using version 0.22.2.post1. This might lead to breaking code or invalid results. Use at your own risk.
  warnings.warn(
/home/doxg/.pyenv/versions/3.8.18/lib/python3.8/site-packages/sklearn/base.py:313: UserWarning: Trying to unpickle estimator TfidfVectorizer from version 1.3.2 when using version 0.22.2.post1. This might lead to breaking code or invalid results. Use at your own risk.
  warnings.warn(


In [ ]:
#     # 미리 계산된 해당 지역의 TF-IDF 행렬 사용
# if question.area == '전체':
#     city_tfidf_matrix = tfidf_matrix
# else:
#     city_tfidf_matrix = city_tfidf_matrices.get(question.area)
#     df = df[df['city']== f'{question.area}']

In [35]:
city_matrices_spot['충남']

<351x5323 sparse matrix of type '<class 'numpy.float64'>'
	with 5212 stored elements in Compressed Sparse Row format>

In [74]:
city_matrices_spot['인천']

<5995x18425 sparse matrix of type '<class 'numpy.float64'>'
	with 5995 stored elements in Compressed Sparse Row format>

In [90]:
area = '인천'
question = '캠핑'

df = spot_df[spot_df['city']== f'{area}']

question_tfidf = vectorizer_spot.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_spot[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]
print(index)


print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



NotFittedError: The TF-IDF vectorizer is not fitted

In [70]:
area = '대구'
question = '피자'

df = food_df[food_df['city']== f'{area}']

question_tfidf = vectorizer_food.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_food[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1][:5]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]



print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



indices=  5
df=  192
2866244 대구 루미너스 0.42204924949455175 모던한 분위기의 한우 안심 스테이크 맛집


In [14]:
np.argsort(cos_similarities[0])[::-1][0]

63

In [15]:
cos_similarities[0][63]

0.30805653331899097

In [27]:
df = pd.read_csv('./travel_spot_v1.csv', index_col=0)

In [29]:
okt = Okt()

In [35]:
question_area = '인천'
question_question = '효도여행'

# 미리 계산된 해당 지역의 TF-IDF 행렬 사용
if question_area == '전체':
    city_tfidf_matrix = tfidf_matrix
else:
    city_tfidf_matrix = city_tfidf_matrices.get(question_area)
    df = df[df['city']== f'{question_area}']

print('여기여기')

if city_tfidf_matrix is None:
    print(JSONResponse(content={"error": f"No data found for city: {question_area}"}, status_code=404))

# 질문과 선택된 지역의 TF-IDF로 유사도 계산
question_tfidf = tfidf_vectorizer.transform(okt.morphs(question_question))
cos_similarities = cosine_similarity(question_tfidf, city_tfidf_matrix)
sorted_indices = np.argsort(cos_similarities[0])[::-1]
len(sorted_indices)

여기여기


352

In [81]:
restaurant = sorted_indices[df.iloc[sorted_indices]['contentType'].eq(39)].tolist()[:5]
non_restaurant = sorted_indices[~df.iloc[sorted_indices]['contentType'].eq(39)].tolist()[:5]

restaurant,non_restaurant

([111, 112, 113, 114, 115], [351, 350, 296, 288, 289])

In [62]:
len(df), len(sorted_indices)

(352, 352)

In [60]:
len(sorted_indices)

352

In [52]:

print('여기여기2')

from itertools import islice
# 식당인 것, 아닌 것
restaurant = islice((index for index in sorted_indices if df.iloc[index]['contentType'] == 39 ), 5)
non_restaurant = islice((index for index in sorted_indices if df.iloc[index]['contentType'] != 39 ), 5)

list(restaurant), list(non_restaurant)

여기여기2


([111, 112, 113, 114, 115], [351, 350, 296, 288, 289])

In [51]:
str(df.iloc[111]['city'])

'인천'

In [55]:
str(df.iloc[111]['id'])

'2758144'

In [53]:
def add_to_similar_tags(sorted_indices,similar_tags):
    bag = []
    for index in sorted_indices:
        print("Current index:", index)
        bag.append({
            "id": str(df.iloc[index]['id']),
            "area": str(df.iloc[index]['city'])})
        similar_tags.append(bag)

In [78]:
restaurant


In [57]:

# 결과를 저장할 리스트 초기화
similar_tags = []
print('여기여기 3')
# 리스트로 추가
def add_to_similar_tags(sorted_indices,similar_tags):
    bag = []
    for index in sorted_indices:
        print("Current index:", index)
        bag.append({
            "id": str(df.iloc[index]['id']),
            "area": str(df.iloc[index]['city']),
            "title": str(df.iloc[index]['title']),
            "similarity": float(cos_similarities[0][index]),
            "catchtitle": str(df.iloc[index]['catchtitle']),
            # "detail": str(df.iloc[index]['detail']),
            "treatMenu": str(df.iloc[index]['treatMenu']),
            "tagName": str(df.iloc[index]['tagName']),
            "addr": str(df.iloc[index]['addr']),
            "info": str(df.iloc[index]['info']),
            # "lat": str(df.iloc[index]['parking']),
            "useTime": str(df.iloc[index]['useTime']),
            "conLike": str(df.iloc[index]['conLike']),
            "conRead": str(df.iloc[index]['conRead']),
            "conShare": str(df.iloc[index]['conShare']),
            # "overView": str(df.iloc[index]['overView']),
            "lat": str(df.iloc[index]['lat']),
            "lon": str(df.iloc[index]['lon'])
            
            })
    similar_tags.append(bag)
print('여기여기4')

# 함수를 사용
add_to_similar_tags(non_restaurant,similar_tags)
add_to_similar_tags(restaurant,similar_tags)
similar_tags

여기여기 3
여기여기4


[[], []]

In [76]:
sorted_indices.__len__()

352

In [73]:
# 결과를 저장할 리스트 초기화
similar_tags = []

def add_to_similar_tags(sorted_indices):
    bag = []
    sorted_indices = list(sorted_indices)[:len(df)]
    print("sorted_indices length:", len(sorted_indices))
    for index in sorted_indices:
        print("Processing index:", index)
        if 0 <= index < len(df):
            print("Adding to bag:", index)
            bag.append({
                "id": str(df.iloc[index]['id']),
                "area": str(df.iloc[index]['city']),
                "title": str(df.iloc[index]['title']),
                "similarity": float(cos_similarities[0][index]),
                "catchtitle": str(df.iloc[index]['catchtitle']),
                "treatMenu": str(df.iloc[index]['treatMenu']),
                "tagName": str(df.iloc[index]['tagName']),
                "addr": str(df.iloc[index]['addr']),
                "info": str(df.iloc[index]['info']),
                "useTime": str(df.iloc[index]['useTime']),
                "conLike": str(df.iloc[index]['conLike']),
                "conRead": str(df.iloc[index]['conRead']),
                "conShare": str(df.iloc[index]['conShare']),
                "lat": str(df.iloc[index]['lat']),
                "lon": str(df.iloc[index]['lon'])
            })
        else:
            print("Index out of bounds:", index)
    print("Adding bag to similar_tags:", bag)
    similar_tags.append(bag)

# 함수를 사용
add_to_similar_tags(non_restaurant)
add_to_similar_tags(restaurant)

print("Final similar_tags:", similar_tags)


sorted_indices length: 0
Adding bag to similar_tags: []
sorted_indices length: 0
Adding bag to similar_tags: []
Final similar_tags: [[], []]
